In [3]:
import os
import time
import glob
from pathlib import Path
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
pd.options.plotting.backend = "plotly" 
import numpy as np
import seaborn as sns
from scipy import stats

ModuleNotFoundError: No module named 'pandas'

In [5]:
if not os.path.exists('output'):
    os.makedirs('output')
if not os.path.exists('plots'):
    os.makedirs('plots')
if not os.path.exists('plots/CPU'):
    os.makedirs('plots/CPU')
if not os.path.exists('plots/Disc'):
    os.makedirs('plots/Disc')
if not os.path.exists('plots/Energy'):
    os.makedirs('plots/Energy')
if not os.path.exists('plots/MEM'):
    os.makedirs('plots/MEM')
if not os.path.exists('plots/Network'):
    os.makedirs('plots/Network')
if not os.path.exists('plots/Network/received'):
    os.makedirs('plots/Network/received')
if not os.path.exists('plots/Network/transmitted'):
    os.makedirs('plots/Network/transmitted')

In [2]:
def plotFigure(dataToUse, colNamesArray, unit, titleText, filePath):
    if len(colNamesArray) > 3:
        print("Too much cols")
        return
    data = dataToUse[colNamesArray]
    data.columns =['L1','L2','L3']
    iteration_plot = data.plot.line(line_shape='hv') # other options: spline / vhv
    iteration_plot.update_xaxes(
        title_text="Time (s)",
        ticktext=["30", "60", "90", "120"],
        tickvals=[data.index[29], data.index[59], data.index[89], data.index.max()]
    )
    iteration_plot.update_yaxes(title_text=unit)
    iteration_plot.update_layout(
        title_text=titleText,
        legend=dict(
            title="Server"
        )
    )
    iteration_plot.write_image(filePath)

In [3]:
def plotBoxplotFigure(data, colNamesArray, title, fileName):
    if len(colNamesArray) > 3:
        print("Too much cols")
        return
    fig = go.Figure()
    fig.add_trace(go.Box(
        x=data[colNamesArray[0]],
        name='L1'
    ))
    fig.add_trace(go.Box(
        x=data[colNamesArray[1]],
        name='L2'
    ))
    fig.add_trace(go.Box(
        x=data[colNamesArray[2]],
        name='L3'
    ))

    fig.update_layout(
        title_text=title,
        xaxis=dict(title='W', zeroline=False),
        boxmode='group',
        legend=dict(
            title="Server"
        )
    )
    fig.update_traces(orientation='h')
    fig.write_image(fileName)

In [4]:
def cleanDataIQR(data):
    Q1=data.quantile(0.25)
    Q3=data.quantile(0.75)
    IQR=Q3-Q1
    lowqe_bound=Q1 - 10 * IQR
    upper_bound=Q3 + 10 * IQR
    return data[~((data < lowqe_bound) |(data > upper_bound))]

In [5]:
l1_matrix = pd.read_csv("./MeasurementFiles/Matrix/Messung_1_L1.csv", sep=";", decimal=",").dropna(axis=1).drop('Nummer', axis=1)
l1_matrix.columns =['Time', 'AVG[W] L1', 'Min[W] L1', 'Max[W] L1']
l1_matrix.index = l1_matrix['Time']
l1_matrix = l1_matrix.drop("Time", axis=1)
l2_matrix = pd.read_csv("./MeasurementFiles/Matrix/Messung_1_L2.csv", sep=";", decimal=",").dropna(axis=1).drop('Nummer', axis=1)
l2_matrix.columns =['Time', 'AVG[W] L2', 'Min[W] L2', 'Max[W] L2']
l2_matrix.index = l2_matrix['Time']
l2_matrix = l2_matrix.drop("Time", axis=1)
l3_matrix = pd.read_csv("./MeasurementFiles/Matrix/Messung_1_L3.csv", sep=";", decimal=",").dropna(axis=1).drop('Nummer', axis=1)
l3_matrix.columns =['Time', 'AVG[W] L3', 'Min[W] L3', 'Max[W] L3']
l3_matrix.index = l3_matrix['Time']
l3_matrix = l3_matrix.drop("Time", axis=1)
matrix = l1_matrix.merge(l2_matrix, on='Time').merge(l3_matrix, on='Time')
print(matrix.shape)
matrix.head()

(123251, 9)


AVG[W] L1  Min[W] L1  Max[W] L1  AVG[W] L2  Min[W] L2  \
Time                                                                       
14.10.20 00:00:01      0.076      0.009      0.148     -0.117     -0.196   
14.10.20 00:00:02      0.100      0.021      0.178     -0.068     -0.209   
14.10.20 00:00:03      0.090      0.002      0.186      0.457     -0.222   
14.10.20 00:00:04      0.073     -0.018      0.131     -0.085     -0.169   
14.10.20 00:00:05      0.106      0.029      0.169     -0.100     -0.223   

                   Max[W] L2  AVG[W] L3  Min[W] L3  Max[W] L3  
Time                                                           
14.10.20 00:00:01      0.037      0.052     -0.075      0.207  
14.10.20 00:00:02      0.007      0.030     -0.132      0.176  
14.10.20 00:00:03      2.782      0.027     -0.130      0.182  
14.10.20 00:00:04      0.019      0.055     -0.066      0.186  
14.10.20 00:00:05      0.027      0.005     -0.139      0.176

In [6]:
cols = ['Date Time','[CPU]Totl%','[MEM]Used','[NET]TxKBTot','[NET]RxKBTot','[DSK]ReadKBTot','[DSK]WriteKBTot']
f1_matrix = pd.read_csv("./MeasurementFiles/Matrix/Network-server-207-F1.csv", sep=";", usecols=cols).dropna(axis=1)#.drop('Nummer', axis=1)
f1_matrix.columns =['Time','CPU% L1','MEM Used L1','KB Transmitted L1','KB Received L1','KB Read L1','KB Write L1']
f1_matrix['Time'] = [time.strftime('%d.%m.%y %H:%M:%S', time.strptime(time_string, '%Y%m%d %H:%M:%S')) for time_string in f1_matrix['Time']]
f1_matrix.index = f1_matrix['Time']
f1_matrix = f1_matrix.drop("Time", axis=1)
f2_matrix = pd.read_csv("./MeasurementFiles/Matrix/Network-server-209-F2.csv", sep=";", usecols=cols).dropna(axis=1)#.drop('Nummer', axis=1)
f2_matrix.columns =['Time','CPU% L2','MEM Used L2','KB Transmitted L2','KB Received L2','KB Read L2','KB Write L2']
f2_matrix['Time'] = [time.strftime('%d.%m.%y %H:%M:%S', time.strptime(time_string, '%Y%m%d %H:%M:%S')) for time_string in f2_matrix['Time']]
f2_matrix.index = f2_matrix['Time']
f2_matrix = f2_matrix.drop("Time", axis=1)
f3_matrix = pd.read_csv("./MeasurementFiles/Matrix/Network-server-208-F3.csv", sep=";", usecols=cols).dropna(axis=1)#.drop('Nummer', axis=1)
f3_matrix.columns =['Time','CPU% L3','MEM Used L3','KB Transmitted L3','KB Received L3','KB Read L3','KB Write L3']
f3_matrix['Time'] = [time.strftime('%d.%m.%y %H:%M:%S', time.strptime(time_string, '%Y%m%d %H:%M:%S')) for time_string in f3_matrix['Time']]
f3_matrix.index = f3_matrix['Time']
f3_matrix = f3_matrix.drop("Time", axis=1)
matrix = matrix.merge(f1_matrix, on='Time', how='outer').merge(f2_matrix, on='Time', how='outer').merge(f3_matrix, on='Time', how='outer').fillna(0)
print(matrix.shape)
matrix.head()

(123251, 27)


AVG[W] L1  Min[W] L1  Max[W] L1  AVG[W] L2  Min[W] L2  \
Time                                                                       
14.10.20 00:00:01      0.076      0.009      0.148     -0.117     -0.196   
14.10.20 00:00:02      0.100      0.021      0.178     -0.068     -0.209   
14.10.20 00:00:03      0.090      0.002      0.186      0.457     -0.222   
14.10.20 00:00:04      0.073     -0.018      0.131     -0.085     -0.169   
14.10.20 00:00:05      0.106      0.029      0.169     -0.100     -0.223   

                   Max[W] L2  AVG[W] L3  Min[W] L3  Max[W] L3  CPU% L1  ...  \
Time                                                                    ...   
14.10.20 00:00:01      0.037      0.052     -0.075      0.207      0.0  ...   
14.10.20 00:00:02      0.007      0.030     -0.132      0.176      0.0  ...   
14.10.20 00:00:03      2.782      0.027     -0.130      0.182      0.0  ...   
14.10.20 00:00:04      0.019      0.055     -0.066      0.186      0.0  ...   
14.10.20 00:00:05      0.027      0.005     -0.139      0.176      0.0  ...   

                   KB Transmitted L2  KB Received L2  KB Read L2  KB Write L2  \
Time                                                                            
14.10.20 00:00:01                0.0             0.0         0.0          0.0   
14.10.20 00:00:02                0.0             0.0         0.0          0.0   
14.10.20 00:00:03                0.0             0.0         0.0          0.0   
14.10.20 00:00:04                0.0             0.0         0.0          0.0   
14.10.20 00:00:05                0.0             0.0         0.0          0.0   

                   CPU% L3  MEM Used L3  KB Transmitted L3  KB Received L3  \
Time                                                                         
14.10.20 00:00:01      0.0          0.0                0.0             0.0   
14.10.20 00:00:02      0.0          0.0                0.0             0.0   
14.10.20 00:00:03      0.0          0.0                0.0             0.0   
14.10.20 00:00:04      0.0          0.0                0.0             0.0   
14.10.20 00:00:05      0.0          0.0                0.0             0.0   

                   KB Read L3  KB Write L3  
Time                                        
14.10.20 00:00:01         0.0          0.0  
14.10.20 00:00:02         0.0          0.0  
14.10.20 00:00:03         0.0          0.0  
14.10.20 00:00:04         0.0          0.0  
14.10.20 00:00:05         0.0          0.0  

[5 rows x 27 columns]

In [7]:
l1_activitypub = pd.read_csv("./MeasurementFiles/ActivityPub/Messung_2_L1.csv", sep=";", decimal=",").dropna(axis=1).drop('Nummer', axis=1)
l1_activitypub.columns =['Time', 'AVG[W] L1', 'Min[W] L1', 'Max[W] L1']
l1_activitypub.index = l1_activitypub['Time']
l1_activitypub = l1_activitypub.drop("Time", axis=1)
l2_activitypub = pd.read_csv("./MeasurementFiles/ActivityPub/Messung_2_L2.csv", sep=";", decimal=",").dropna(axis=1).drop('Nummer', axis=1)
l2_activitypub.columns =['Time', 'AVG[W] L2', 'Min[W] L2', 'Max[W] L2']
l2_activitypub.index = l2_activitypub['Time']
l2_activitypub = l2_activitypub.drop("Time", axis=1)
l3_activitypub = pd.read_csv("./MeasurementFiles/ActivityPub/Messung_2_L3.csv", sep=";", decimal=",").dropna(axis=1).drop('Nummer', axis=1)
l3_activitypub.columns =['Time', 'AVG[W] L3', 'Min[W] L3', 'Max[W] L3']
l3_activitypub.index = l3_activitypub['Time']
l3_activitypub = l3_activitypub.drop("Time", axis=1)
activitypub = l1_activitypub.merge(l2_activitypub, on='Time').merge(l3_activitypub, on='Time')
activitypub.head()

AVG[W] L1  Min[W] L1  Max[W] L1  AVG[W] L2  Min[W] L2  \
Time                                                                       
15.10.20 00:00:01      9.157      7.878     13.265      6.515      6.004   
15.10.20 00:00:02      8.819      7.424     12.104      6.643      5.986   
15.10.20 00:00:03      8.238      7.494      8.660      6.199      5.304   
15.10.20 00:00:04      8.269      7.554      8.916      6.522      6.175   
15.10.20 00:00:05      8.378      7.808      8.852      6.450      6.222   

                   Max[W] L2  AVG[W] L3  Min[W] L3  Max[W] L3  
Time                                                           
15.10.20 00:00:01      6.963      7.210      6.939      7.701  
15.10.20 00:00:02      8.129      9.163      7.199     13.603  
15.10.20 00:00:03      6.595      7.501      7.057      8.369  
15.10.20 00:00:04      6.811      7.221      6.728      7.801  
15.10.20 00:00:05      6.800      7.229      6.982      7.485

In [8]:
cols = ['Date Time','[CPU]Totl%','[MEM]Used','[NET]TxKBTot','[NET]RxKBTot','[DSK]ReadKBTot','[DSK]WriteKBTot']
f1_activitypub = pd.read_csv("./MeasurementFiles/ActivityPub/Network-server-207-F1.csv", sep=";", usecols=cols).dropna(axis=1)
f1_activitypub.columns =['Time','CPU% L1','MEM Used L1','KB Transmitted L1','KB Received L1','KB Read L1','KB Write L1']
f1_activitypub['Time'] = [time.strftime('%d.%m.%y %H:%M:%S', time.strptime(time_string, '%Y%m%d %H:%M:%S')) for time_string in f1_activitypub['Time']]
f1_activitypub.index = f1_activitypub['Time']
f1_activitypub = f1_activitypub.drop("Time", axis=1)
f2_activitypub = pd.read_csv("./MeasurementFiles/ActivityPub/Network-server-209-F2.csv", sep=";", usecols=cols).dropna(axis=1)
f2_activitypub.columns =['Time','CPU% L2','MEM Used L2','KB Transmitted L2','KB Received L2','KB Read L2','KB Write L2']
f2_activitypub['Time'] = [time.strftime('%d.%m.%y %H:%M:%S', time.strptime(time_string, '%Y%m%d %H:%M:%S')) for time_string in f2_activitypub['Time']]
f2_activitypub.index = f2_activitypub['Time']
f2_activitypub = f2_activitypub.drop("Time", axis=1)
f3_activitypub = pd.read_csv("./MeasurementFiles/ActivityPub/Network-server-208-F3.csv", sep=";", usecols=cols).dropna(axis=1)
f3_activitypub.columns =['Time','CPU% L3','MEM Used L3','KB Transmitted L3','KB Received L3','KB Read L3','KB Write L3']
f3_activitypub['Time'] = [time.strftime('%d.%m.%y %H:%M:%S', time.strptime(time_string, '%Y%m%d %H:%M:%S')) for time_string in f3_activitypub['Time']]
f3_activitypub.index = f3_activitypub['Time']
f3_activitypub = f3_activitypub.drop("Time", axis=1)
activitypub = activitypub.merge(f1_activitypub, on='Time', how='outer').merge(f2_activitypub, on='Time', how='outer').merge(f3_activitypub, on='Time', how='outer').fillna(0)
print(activitypub.shape)
activitypub.head()

(142191, 27)


AVG[W] L1  Min[W] L1  Max[W] L1  AVG[W] L2  Min[W] L2  \
Time                                                                       
15.10.20 00:00:01      9.157      7.878     13.265      6.515      6.004   
15.10.20 00:00:02      8.819      7.424     12.104      6.643      5.986   
15.10.20 00:00:03      8.238      7.494      8.660      6.199      5.304   
15.10.20 00:00:04      8.269      7.554      8.916      6.522      6.175   
15.10.20 00:00:05      8.378      7.808      8.852      6.450      6.222   

                   Max[W] L2  AVG[W] L3  Min[W] L3  Max[W] L3  CPU% L1  ...  \
Time                                                                    ...   
15.10.20 00:00:01      6.963      7.210      6.939      7.701      0.0  ...   
15.10.20 00:00:02      8.129      9.163      7.199     13.603      0.0  ...   
15.10.20 00:00:03      6.595      7.501      7.057      8.369      0.0  ...   
15.10.20 00:00:04      6.811      7.221      6.728      7.801      0.0  ...   
15.10.20 00:00:05      6.800      7.229      6.982      7.485      0.0  ...   

                   KB Transmitted L2  KB Received L2  KB Read L2  KB Write L2  \
Time                                                                            
15.10.20 00:00:01                0.0             0.0         0.0          0.0   
15.10.20 00:00:02                0.0             0.0         0.0          0.0   
15.10.20 00:00:03                0.0             0.0         0.0          0.0   
15.10.20 00:00:04                0.0             0.0         0.0          0.0   
15.10.20 00:00:05                0.0             0.0         0.0          0.0   

                   CPU% L3  MEM Used L3  KB Transmitted L3  KB Received L3  \
Time                                                                         
15.10.20 00:00:01      0.0          0.0                0.0             0.0   
15.10.20 00:00:02      0.0          0.0                0.0             0.0   
15.10.20 00:00:03      0.0          0.0                0.0             0.0   
15.10.20 00:00:04      0.0          0.0                0.0             0.0   
15.10.20 00:00:05      0.0          0.0                0.0             0.0   

                   KB Read L3  KB Write L3  
Time                                        
15.10.20 00:00:01         0.0          0.0  
15.10.20 00:00:02         0.0          0.0  
15.10.20 00:00:03         0.0          0.0  
15.10.20 00:00:04         0.0          0.0  
15.10.20 00:00:05         0.0          0.0  

[5 rows x 27 columns]

In [9]:
frames = [matrix, activitypub]
result = pd.concat(frames)
result = result[~result.index.duplicated(keep='first')]
result.to_csv("output/MeasurementData.csv")
print(result.shape)
result.head()

(228591, 27)


AVG[W] L1  Min[W] L1  Max[W] L1  AVG[W] L2  Min[W] L2  \
Time                                                                       
14.10.20 00:00:01      0.076      0.009      0.148     -0.117     -0.196   
14.10.20 00:00:02      0.100      0.021      0.178     -0.068     -0.209   
14.10.20 00:00:03      0.090      0.002      0.186      0.457     -0.222   
14.10.20 00:00:04      0.073     -0.018      0.131     -0.085     -0.169   
14.10.20 00:00:05      0.106      0.029      0.169     -0.100     -0.223   

                   Max[W] L2  AVG[W] L3  Min[W] L3  Max[W] L3  CPU% L1  ...  \
Time                                                                    ...   
14.10.20 00:00:01      0.037      0.052     -0.075      0.207      0.0  ...   
14.10.20 00:00:02      0.007      0.030     -0.132      0.176      0.0  ...   
14.10.20 00:00:03      2.782      0.027     -0.130      0.182      0.0  ...   
14.10.20 00:00:04      0.019      0.055     -0.066      0.186      0.0  ...   
14.10.20 00:00:05      0.027      0.005     -0.139      0.176      0.0  ...   

                   KB Transmitted L2  KB Received L2  KB Read L2  KB Write L2  \
Time                                                                            
14.10.20 00:00:01                0.0             0.0         0.0          0.0   
14.10.20 00:00:02                0.0             0.0         0.0          0.0   
14.10.20 00:00:03                0.0             0.0         0.0          0.0   
14.10.20 00:00:04                0.0             0.0         0.0          0.0   
14.10.20 00:00:05                0.0             0.0         0.0          0.0   

                   CPU% L3  MEM Used L3  KB Transmitted L3  KB Received L3  \
Time                                                                         
14.10.20 00:00:01      0.0          0.0                0.0             0.0   
14.10.20 00:00:02      0.0          0.0                0.0             0.0   
14.10.20 00:00:03      0.0          0.0                0.0             0.0   
14.10.20 00:00:04      0.0          0.0                0.0             0.0   
14.10.20 00:00:05      0.0          0.0                0.0             0.0   

                   KB Read L3  KB Write L3  
Time                                        
14.10.20 00:00:01         0.0          0.0  
14.10.20 00:00:02         0.0          0.0  
14.10.20 00:00:03         0.0          0.0  
14.10.20 00:00:04         0.0          0.0  
14.10.20 00:00:05         0.0          0.0  

[5 rows x 27 columns]

In [10]:
measurement_files = Path("MeasurementFiles").rglob('*.csv')
summary = pd.DataFrame()
baseline = None
maxW = None
minW = None
for measurement_file in measurement_files:
    measurement_avg = None
    if "Messung" in measurement_file.name or "Network" in measurement_file.name:
        continue
    measurement_name = measurement_file.name.split(" ")[1]
    if "Windows" in measurement_file.name:
        measurement_name = measurement_name + " Windows"
    elif "Matrix" in measurement_file.name:
        measurement_name = measurement_name + " Matrix"
    elif "ActivityPub" in measurement_file.name:
        measurement_name = measurement_name + " ActivityPub"
    print(measurement_name)
    csv_data = pd.read_csv(measurement_file.absolute()).dropna(axis=1)
    start_measurement_string = time.strftime('%d.%m.%y %H:%M:%S', time.localtime(int(csv_data["Start"][0])))
    end_measurement_string = time.strftime('%d.%m.%y %H:%M:%S', time.localtime(int(csv_data["End"][len(csv_data["End"]) - 1])))
    measurement_data = result.loc[start_measurement_string:end_measurement_string]

    plotBoxplotFigure(measurement_data, ["AVG[W] L1", "AVG[W] L2", "AVG[W] L3"], measurement_name + " Energy before cleaning", "plots/Energy/" + measurement_name + " Boxplot.png")
    measurement_data["AVG[W] L1"] = cleanDataIQR(measurement_data["AVG[W] L1"])
    measurement_data["AVG[W] L2"] = cleanDataIQR(measurement_data["AVG[W] L2"])
    measurement_data["AVG[W] L3"] = cleanDataIQR(measurement_data["AVG[W] L3"])
    plotBoxplotFigure(measurement_data, ["AVG[W] L1", "AVG[W] L2", "AVG[W] L3"], measurement_name + " Energy after cleaning", "plots/Energy/" + measurement_name + " Boxplot cleaned.png")
    
    plotBoxplotFigure(measurement_data, ["KB Received L1", "KB Received L2", "KB Received L3"], measurement_name + " Network before cleaning", "plots/Network/received/" + measurement_name + " Boxplot.png")
    if "Baseline" not in measurement_name and "Windows" not in measurement_name:
        measurement_data["KB Received L1"] = measurement_data.loc[stats.zscore(measurement_data["KB Received L1"]) <= 3]["KB Received L1"]
        measurement_data["KB Received L2"] = measurement_data.loc[stats.zscore(measurement_data["KB Received L2"]) <= 3]["KB Received L2"]
        measurement_data["KB Received L3"] = measurement_data.loc[stats.zscore(measurement_data["KB Received L3"]) <= 3]["KB Received L3"]
    plotBoxplotFigure(measurement_data, ["KB Received L1", "KB Received L2", "KB Received L3"], measurement_name + " Network after cleaning", "plots/Network/received/" + measurement_name + " Boxplot cleaned.png")

    measurement_results = pd.DataFrame()
    iteration_count = 0
    for measurement_row in csv_data.to_numpy():
        title = measurement_name + " " + str(measurement_row[0])
        start_string = time.strftime('%d.%m.%y %H:%M:%S', time.localtime(int(measurement_row[1]) + 2))
        end_string = time.strftime('%d.%m.%y %H:%M:%S', time.localtime(int(measurement_row[2]) - 1))
        iteration_data = measurement_data.loc[start_string:end_string]

        plotFigure(iteration_data, ["AVG[W] L1","AVG[W] L2","AVG[W] L3"], "Energy (W)", "Energy " + title, "plots/Energy/" + title + ".png")
        plotFigure(iteration_data, ["CPU% L1","CPU% L2","CPU% L3"], "Workload (%)", "CPU " + title, "plots/CPU/" + title + ".png")
        plotFigure(iteration_data, ["MEM Used L1","MEM Used L2","MEM Used L3"], "Usage (MByte)", "Memory " + title, "plots/MEM/" + title + ".png")
        plotFigure(iteration_data, ["KB Transmitted L1","KB Transmitted L2","KB Transmitted L3"], "Transmitted (KB)", "Network Send " + title, "plots/Network/transmitted/" + title + " transmitted.png")
        plotFigure(iteration_data, ["KB Received L1","KB Received L2","KB Received L3"], "Received (KB)", "Network Received " + title, "plots/Network/received/" + title + " received.png")
        plotFigure(iteration_data, ["KB Read L1","KB Read L2","KB Read L3"], "Read (KB)", "Disc Read " + title, "plots/Disc/" + title + " read.png")
        plotFigure(iteration_data, ["KB Write L1","KB Write L2","KB Write L3"], "Write (KB)", "Disc Write " + title, "plots/Disc/" + title + " write.png")
        iteration = iteration_data.mean()

        iteration["Energy L1"] = iteration["AVG[W] L1"] + (((iteration["KB Received L1"] / 1000000) / 0.025634766) * 52 * 3600) + ((iteration["KB Received L1"] / 1000000) * 0.052 * 0.25 * 3600000)
        iteration["Energy L2"] = iteration["AVG[W] L2"] + (((iteration["KB Received L2"] / 1000000) / 0.025634766) * 52 * 3600) + ((iteration["KB Received L2"] / 1000000) * 0.052 * 0.25 * 3600000)
        iteration["Energy L3"] = iteration["AVG[W] L3"] + (((iteration["KB Received L3"] / 1000000) / 0.025634766) * 52 * 3600) + ((iteration["KB Received L3"] / 1000000) * 0.052 * 0.25 * 3600000)

        iteration['Iteration'] = int(measurement_row[0])
        measurement_results = measurement_results.append(iteration, ignore_index=True)

        if baseline is not None:
            baselineTotal = baseline["Energy L1"] + baseline["Energy L2"] + baseline["Energy L3"]
            iteration["Energy total"] = iteration["Energy L1"] + iteration["Energy L2"] + iteration["Energy L3"] - baselineTotal
            if "Baseline" not in measurement_name and "Windows" not in measurement_name:
                iteration["Actions Send"] = int(measurement_row[3])
                energyEfficiency = iteration["Energy total"] / (iteration["Actions Send"] / 120)
                if maxW is None or energyEfficiency > (maxW["Energy total"] / (maxW["Actions Send"] / 120)):
                    maxW = iteration

                if minW is None or energyEfficiency < (minW["Energy total"] / (minW["Actions Send"] / 120)):
                    minW = iteration

        iteration_data = iteration_data.reset_index()
        del iteration_data["Time"]
        if measurement_avg is None:
            measurement_avg = iteration_data
        else:
            measurement_avg = measurement_avg + iteration_data.fillna(0)
        iteration_count = iteration_count + 1
    measurement_avg = measurement_avg / iteration_count
    plotFigure(measurement_avg, ["AVG[W] L1","AVG[W] L2","AVG[W] L3"], "Energy (W)", "Energy " + measurement_name, "plots/Energy/" + measurement_name + ".png")
    plotFigure(measurement_avg, ["CPU% L1","CPU% L2","CPU% L3"], "Workload (%)", "CPU " + measurement_name, "plots/CPU/" + measurement_name + ".png")
    plotFigure(measurement_avg, ["MEM Used L1","MEM Used L2","MEM Used L3"], "Usage (MByte)", "Memory " + measurement_name, "plots/MEM/" + measurement_name + ".png")
    plotFigure(measurement_avg, ["KB Transmitted L1","KB Transmitted L2","KB Transmitted L3"], "Transmitted (KB)", "Network Send " + measurement_name, "plots/Network/transmitted/" + measurement_name + " transmitted.png")
    plotFigure(measurement_avg, ["KB Received L1","KB Received L2","KB Received L3"], "Received (KB)", "Network Received " + measurement_name, "plots/Network/received/" + measurement_name + " received.png")
    plotFigure(measurement_avg, ["KB Read L1","KB Read L2","KB Read L3"], "Read (KB)", "Disc Read " + measurement_name, "plots/Disc/" + measurement_name + " read.png")
    plotFigure(measurement_avg, ["KB Write L1","KB Write L2","KB Write L3"], "Write (KB)", "Disc Write " + measurement_name, "plots/Disc/" + measurement_name + " write.png")
    csv_data = csv_data.merge(measurement_results)
    csv_data_mean = csv_data.mean()
    csv_data = csv_data.append(csv_data_mean, ignore_index=True)
    csv_data.to_csv(measurement_file.name)
    if "Windows" not in measurement_name:
        if "Baseline" in measurement_name:
            baseline = csv_data_mean
        else:
            csv_data_mean["Measurement"] = measurement_name
            cols_name = ["Measurement","Actions Send","AVG[W] L1","AVG[W] L2","AVG[W] L3","Energy L1","Energy L2","Energy L3","CPU% L1","CPU% L2","CPU% L3","MEM Used L1","MEM Used L2","MEM Used L3","KB Received L1","KB Received L2","KB Received L3","KB Write L1","KB Write L2","KB Write L3"]
            summary = summary.append(csv_data_mean[cols_name], ignore_index=True)
if baseline is not None:
    print("baseline")
    print(baseline)
    print("min")
    print(minW)
    minW["Energy Efficiency"] = minW["Energy total"] / (minW["Actions Send"] / 120)
    print(minW["Energy Efficiency"])
    print("max")
    print(maxW)
    maxW["Energy Efficiency"] = maxW["Energy total"] / (maxW["Actions Send"] / 120)
    print(maxW["Energy Efficiency"])
    for key in summary:
        if key != "Measurement" and key != "Actions Send":
            baseline_values = []
            for value in summary[key]:
                baseline_values.append(baseline[key])
            summary[key + " without Baseline"] = summary[key] - baseline_values
    summary["Energy total"] = summary["Energy L1 without Baseline"] + summary["Energy L2 without Baseline"] + summary["Energy L3 without Baseline"]
    summary["Energy Efficiency"] = summary["Energy total"] / (summary["Actions Send"] / 120)
    summary["Energy Efficiency normalized"] = (summary["Energy Efficiency"] - minW["Energy Efficiency"])/(maxW["Energy Efficiency"] - minW["Energy Efficiency"])
    summary["CPU% total"] = summary["CPU% L1 without Baseline"] + summary["CPU% L2 without Baseline"] + summary["CPU% L3 without Baseline"]
    summary["MEM Used total"] = summary["MEM Used L1 without Baseline"] + summary["MEM Used L2 without Baseline"] + summary["MEM Used L3 without Baseline"]
    summary["KB Received total"] = summary["KB Received L1 without Baseline"] + summary["KB Received L2 without Baseline"] + summary["KB Received L3 without Baseline"]
    summary["KB Write total"] = summary["KB Write L1 without Baseline"] + summary["KB Write L2 without Baseline"] + summary["KB Write L3 without Baseline"]
summary.to_csv("summary.csv")

111111111 Windows
Baseline Windows
Baseline
121110101 ActivityPub
112110101 ActivityPub
211110101 ActivityPub
111110101 ActivityPub
111010101 ActivityPub
111210101 ActivityPub
110110101 ActivityPub
011110101 ActivityPub
101110101 ActivityPub
211111111 Matrix
121111111 Matrix
111111011 Matrix
011111111 Matrix
111011111 Matrix
112111111 Matrix
111111101 Matrix
101111111 Matrix
111110111 Matrix
111211111 Matrix
111111111 Matrix
110111111 Matrix
baseline
Iteration            5.500000e+00
Start                1.602788e+09
End                  1.602788e+09
AVG[W] L1            5.950951e+00
AVG[W] L2            4.132172e+00
AVG[W] L3            5.818045e+00
CPU% L1              5.080473e-02
CPU% L2              2.116508e-02
CPU% L3              4.742914e-02
Energy L1            5.950951e+00
Energy L2            4.132172e+00
Energy L3            5.818045e+00
KB Read L1           0.000000e+00
KB Read L2           0.000000e+00
KB Read L3           0.000000e+00
KB Received L1       0.000000e+00
K

In [11]:
categories = ['Q1.1','Q1.2','Q1.3', 'Q2.1', 'Q2.2', 'Q3.1', 'Q4.1', 'Q4.2', 'Q4.3']

fig = go.Figure()

fig.add_trace(go.Scatterpolar(
      r=[0.3313,0.3313,0.3313,0.3313,0.3313,0.3313,0.3313,0.3313,0.3313],
      theta=categories,
      fill='toself',
      name='Average'
))
fig.add_trace(go.Scatterpolar(
      r=[0.3478,0.3651,0.3333,0.3738,0.3313,0.3313,0.3313,0.3313,0.3313],
      theta=categories,
      fill='toself',
      name='Worst'
))
fig.add_trace(go.Scatterpolar(
      r=[0.2806,0.2578,0.0110,0.3291,0.3313,0.3310,0.2790,0.2782,0.3313],
      theta=categories,
      fill='toself',
      name='Best'
))

fig.update_layout(
  title_text="Matrix",
  polar=dict(
    angularaxis=dict(
        direction="clockwise"
    ),
    radialaxis=dict(
      visible=True,
      range=[0, 1],
      tickmode="array",
      tickvals=[0, 1],
      ticktext=[0, 1]
    )),
  showlegend=True
)

fig.write_image("Radar Matrix.png")

In [12]:
categories = ['Q1.1','Q1.2','Q1.3', 'Q2.1', 'Q2.2', 'Q3.1', 'Q4.1', 'Q4.2', 'Q4.3']

fig = go.Figure()

fig.add_trace(go.Scatterpolar(
      r=[0.2926,0.2926,0.2926,0.2926,0.2926,0.2926,0.2926,0.2926,0.2926],
      theta=categories,
      fill='toself',
      name='Average'
))
fig.add_trace(go.Scatterpolar(
      r=[0.2708,0.3015,0.9479,0.3451,0.2926,0.2926,0.2926,0.2926,0.2926],
      theta=categories,
      fill='toself',
      name='Worst'
))
fig.add_trace(go.Scatterpolar(
      r=[0.2930,0.2199,0.0013,0.2269,0.2926,0.2926,0.2926,0.2926,0.2926],
      theta=categories,
      fill='toself',
      name='Best'
))

fig.update_layout(
  title_text="ActivityPub",
  polar=dict(
    angularaxis=dict(
        direction="clockwise"
    ),
    radialaxis=dict(
      visible=True,
      range=[0, 1],
      tickmode="array",
      tickvals=[0, 1],
      ticktext=[0, 1]
    )),
  showlegend=True
)

fig.write_image("Radar ActivityPub.png")

In [13]:
print("End")

End
